In [ ]:
import librosa
import os
import numpy as np
import re

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import pandas as pd

### Import Speaker Metadata

In [ ]:
meta = pd.read_csv('drive/MyDrive/speakers_all.csv')
display(meta)

age  age_onset              birthplace  filename native_language  \
0     24.0       12.0         koussi, senegal   balanta         balanta   
1     18.0       10.0          buea, cameroon  cameroon        cameroon   
2     48.0        8.0  hong, adamawa, nigeria  fulfulde        fulfulde   
3     42.0       42.0   port-au-prince, haiti   haitian         haitian   
4     40.0       35.0   port-au-prince, haiti   haitian         haitian   
...    ...        ...                     ...       ...             ...   
2167  46.0        5.0          lagos, nigeria   yoruba3          yoruba   
2168  46.0       12.0          lagos, nigeria   yoruba4          yoruba   
2169  47.0        2.0         ibadan, nigeria   yoruba5          yoruba   
2170  31.0        1.0     bethel, alaska, usa    yupik1           yupik   
2171  24.0       14.0      bulawayo, zimbabwe     zulu1            zulu   

         sex  speakerid   country  file_missing?  Unnamed: 9  Unnamed: 10  \
0       male        788   senegal           True         NaN          NaN   
1       male       1953  cameroon           True         NaN          NaN   
2       male       1037   nigeria           True         NaN          NaN   
3       male       1165     haiti           True         NaN          NaN   
4       male       1166     haiti           True         NaN          NaN   
...      ...        ...       ...            ...         ...          ...   
2167  female        766   nigeria          False         NaN          NaN   
2168    male        851   nigeria          False         NaN          NaN   
2169  female       2023   nigeria          False         NaN          NaN   
2170  female        571       usa          False         NaN          NaN   
2171  female        406  zimbabwe          False         NaN          NaN   

     Unnamed: 11  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  
...          ...  
2167         NaN  
2168         NaN  
2169         NaN  
2170         NaN  
2171         NaN  

[2172 rows x 12 columns]

In [ ]:
lang_list = list(meta['native_language'].value_counts().keys()[:6])
print(lang_list)

['english', 'spanish', 'arabic', 'mandarin', 'french', 'korean']


### Import Audio Data

In [ ]:
! unzip "/content/drive/MyDrive/recordings2.zip" -d "/content"

Archive:  /content/drive/MyDrive/recordings2.zip
   creating: /content/output/
  inflating: /content/output/russian12.wav  
  inflating: /content/output/nepali2.wav  
  inflating: /content/output/armenian4.wav  
  inflating: /content/output/amharic15.wav  
  inflating: /content/output/english101.wav  
  inflating: /content/output/romanian6.wav  
  inflating: /content/output/german19.wav  
  inflating: /content/output/french14.wav  
  inflating: /content/output/mandarin3.wav  
  inflating: /content/output/english7.wav  
  inflating: /content/output/english115.wav  
  inflating: /content/output/miskito8.wav  
  inflating: /content/output/german25.wav  
  inflating: /content/output/french28.wav  
  inflating: /content/output/german31.wav  
  inflating: /content/output/vietnamese17.wav  
  inflating: /content/output/english129.wav  
  inflating: /content/output/cantonese9.wav  
  inflating: /content/output/arabic96.wav  
  inflating: /content/output/arabic82.wav  
  inflating: /content/out

### Generate MFCC Embeddings

In [ ]:
#MFCCs

directory = 'output'
mfccss = []
labels = []
max_dim = 0
min_dim = np.float("inf")

# iterate over files in directory
for filename in os.listdir(directory):

    #print(filename)

    #only include files with speakers from lang_list
    lang = meta[meta['filename'] + ".wav" == filename]['native_language'].values[0]

    if lang in lang_list:
        labels.append(lang)

        f = os.path.join(directory, filename)
        x, sr = librosa.load(f)

        #compute mfcss
        mfccs = librosa.feature.mfcc(y = x, sr =sr , n_mfcc = 40)

        max_dim = max(max_dim, mfccs.shape[1])
        min_dim = min(min_dim, mfccs.shape[1])
        mfccss.append(mfccs)



<ipython-input-41-8faaaa495ecf>:7: DeprecationWarning:

`np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations



In [47]:
#print(labels)
#print(len(labels))

## Pad MFCCS

In [ ]:
#resize mfccs to all be the same size
resized_mfccs = []
for mfcc in mfccss:
  rs = librosa.util.fix_length(data=mfcc, size=max_dim, axis=1)
  resized_mfccs.append(rs.flatten())

resized_mfccs = np.array(resized_mfccs)
print(resized_mfccs.shape)

(1023, 146640)


#Clustering

## PCA

In [ ]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import MinMaxScaler, StandardScaler
import matplotlib.pyplot as plt
import plotly.express as px

In [ ]:
pca = PCA(n_components=3)
transformed = pca.fit_transform(resized_mfccs)

In [ ]:
print(transformed.shape)

(1023, 3)


In [ ]:
pca.explained_variance_ratio_

array([0.2639865 , 0.06861805, 0.04019303], dtype=float32)

In [ ]:
#Plot results
fig = px.scatter_3d(transformed, x=0, y=1, z= 2, color = labels, title = "PCA of MFCC")
fig.show()

### PCA Clustering Metrics

In [ ]:
def clustering_metrics(labels, transformed):
  lang_to_comps = {}
  for lang, comp in zip(labels, transformed):
    if lang not in lang_to_comps:
        lang_to_comps[lang] = [comp]
    else:
        lang_to_comps[lang].append(comp)

  #calculate cluster centroids
  lang_to_centroid = {}
  for lang in lang_to_comps:
    centroid = np.average(np.asarray(lang_to_comps[lang]), axis = 0)
    lang_to_centroid[lang] = centroid


  #standard deviations
  for lang in lang_to_comps:
    std = np.std(np.asarray(lang_to_comps[lang]))
    print(lang.upper(), "standard deviation: ", std)

  print("\n")

  #pairwise cluster distances
  for i in range(len(lang_list)):
    centroid = lang_to_centroid[lang_list[i]]
    #english_centroid = lang_to_centroid['english']
    for j in range(i+1, len(lang_list)):
      #if lang != l:
      distance = np.linalg.norm(lang_to_centroid[lang_list[j]] - centroid)
      print(lang_list[i].upper() + "-" + lang_list[j].upper() + ' distance : ', distance)




In [ ]:
clustering_metrics(labels, transformed)

ENGLISH standard deviation:  1764.3357
SPANISH standard deviation:  2773.039
ARABIC standard deviation:  3111.8152
FRENCH standard deviation:  2003.447
MANDARIN standard deviation:  2747.981
KOREAN standard deviation:  2701.9294


ENGLISH-SPANISH distance :  3282.56
ENGLISH-ARABIC distance :  4952.708
ENGLISH-MANDARIN distance :  3931.917
ENGLISH-FRENCH distance :  2076.2822
ENGLISH-KOREAN distance :  3649.187
SPANISH-ARABIC distance :  1708.4034
SPANISH-MANDARIN distance :  679.21906
SPANISH-FRENCH distance :  1445.0956
SPANISH-KOREAN distance :  463.01892
ARABIC-MANDARIN distance :  1201.8525
ARABIC-FRENCH distance :  3090.0435
ARABIC-KOREAN distance :  1471.4573
MANDARIN-FRENCH distance :  2039.7697
MANDARIN-KOREAN distance :  373.43036
FRENCH-KOREAN distance :  1699.0164


## tSNE

In [ ]:
from sklearn.manifold import TSNE

tSNE Hyperparameter Tuning

In [ ]:
#experiment with different hyperparameters

perplexities = [2, 5, 30, 50, 100]
iterations = [500, 1000, 2000, 5000]
lr = [10, 50, 100]

for p in perplexities:
  for i in iterations:
    for l in lr:
        tsne = TSNE(n_components = 3, perplexity=p, learning_rate = l, n_iter = i).fit_transform(resized_mfccs)
        print("Hyperparameters: perplexity = " + str(p) + " iterations = " + str(i) + " lr = " + str(l))

        fig = px.scatter_3d(tsne, x=0, y=1, z=2, color = labels)
        fig.show()


Hyperparameters: perplexity = 2 iterations = 500 lr = 10


Hyperparameters: perplexity = 2 iterations = 500 lr = 50


Hyperparameters: perplexity = 2 iterations = 500 lr = 100


Hyperparameters: perplexity = 2 iterations = 1000 lr = 10


Hyperparameters: perplexity = 2 iterations = 1000 lr = 50


...

Hyperparameters: perplexity = 100 iterations = 2000 lr = 50


Hyperparameters: perplexity = 100 iterations = 2000 lr = 100


Hyperparameters: perplexity = 100 iterations = 5000 lr = 10


Hyperparameters: perplexity = 100 iterations = 5000 lr = 50


Hyperparameters: perplexity = 100 iterations = 5000 lr = 100


### Final tSNE

In [ ]:
tsne = TSNE(n_components = 3, perplexity=50, learning_rate = 10, n_iter = 5000).fit_transform(resized_mfccs)

fig = px.scatter_3d(tsne, x=0, y=1, z=2, color = labels, title = "tSNE of MFCC")
fig.show()

clustering_metrics(labels, tsne)

ENGLISH standard deviation:  7.6470876
SPANISH standard deviation:  10.153739
ARABIC standard deviation:  10.474582
FRENCH standard deviation:  8.353755
MANDARIN standard deviation:  10.374387
KOREAN standard deviation:  9.692527


ENGLISH-SPANISH distance :  14.048189
ENGLISH-ARABIC distance :  20.79863
ENGLISH-MANDARIN distance :  17.846718
ENGLISH-FRENCH distance :  10.840466
ENGLISH-KOREAN distance :  17.529198
SPANISH-ARABIC distance :  6.7553864
SPANISH-MANDARIN distance :  3.9061403
SPANISH-FRENCH distance :  3.2434125
SPANISH-KOREAN distance :  3.4817305
ARABIC-MANDARIN distance :  3.1347134
ARABIC-FRENCH distance :  9.977184
ARABIC-KOREAN distance :  3.276609
MANDARIN-FRENCH distance :  7.129323
MANDARIN-KOREAN distance :  1.0119945
FRENCH-KOREAN distance :  6.712604


In [ ]:
#numerically encode labels
nums = []
for l in labels:
  if l == "english":
    nums.append(1)
  elif l == "spanish":
    nums.append(2)
  elif l == "arabic":
    nums.append(3)
  elif l == "french":
    nums.append(4)
  elif l == "madarin":
    nums.append(5)
  else:
    nums.append(6)


In [ ]:
from sklearn.metrics import r2_score
from sklearn.cross_decomposition import PLSRegression

#Variance explained by tSNE
tSNE_matrix = pd.DataFrame(tsne[:, 0])
pls1 = PLSRegression(n_components = 1)
pls1.fit(tSNE_matrix, nums)
y_pred1 = pls1.predict(tSNE_matrix)
print(r2_score(nums, y_pred1, multioutput = 'variance_weighted'))

tSNE_matrix = pd.DataFrame(tsne[:, 1])
pls2 = PLSRegression(n_components = 1)
pls2.fit(tSNE_matrix, nums)
y_pred2 = pls2.predict(tSNE_matrix)
print(r2_score(nums, y_pred2, multioutput = 'variance_weighted'))

tSNE_matrix = pd.DataFrame(tsne[:, 2])
pls3 = PLSRegression(n_components = 1)
pls3.fit(tSNE_matrix, nums)
y_pred3 = pls3.predict(tSNE_matrix)
print(r2_score(nums, y_pred3, multioutput = 'variance_weighted'))


0.1758354919048839
0.05125805900950264
0.0086266282953823


### UMAP

In [ ]:
!pip install umap-learn

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.2/88.2 kB 3.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 19.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for umap-learn: filename=umap_learn-0.5.3-py3-none-any.whl size=82816 sha256=3e54e7f15c1c0ff1252fdd66e81cf8e6884d7965225cd5d6ef3c715adfe70fe3
  Stored in directory: /root/.cache/pip/wheels/a0/e8/c6/a37ea663620bd5200ea1ba0907ab3c217042c1d035ef606acc
  Created wheel for pynndescent: filename=pynndescent-0.5.10-py3-none-any.whl size=55622 sha256=ce6ba5fc8c8049c56faf50d30d8b20291f670aac9a8200c1ab17fa1eca2b97e8
  Stored in directory: /root/.cache/pip/wheels/4a/38/5d/f60a40a66a9512b7e5e83517ebc2d1b42d857be97d135f1096
Successfully built umap-learn pynndescent


In [ ]:
import umap.umap_ as umap

### UMAP Hyperparamter Tuning

In [ ]:
distances = [0, .001, .01, .1, .5]
neighbors = [5, 15, 50, 100, 150]
metric = ["euclidean"]

for n in neighbors:
  for d in distances:
    for m in metric:
      u = umap.UMAP(n_components = 3, n_neighbors = n, min_dist = d, metric = m).fit_transform(resized_mfccs)
      print("Hyperparameters: neighbors = " + str(n) + " distances = " + str(d) + "metric = " + str(m))
      fig = px.scatter_3d(u, x=0, y=1, z=2, color = labels)
      fig.show()


Hyperparameters: neighbors = 5 distances = 0metric = euclidean


Hyperparameters: neighbors = 5 distances = 0.001metric = euclidean


Hyperparameters: neighbors = 5 distances = 0.01metric = euclidean


Hyperparameters: neighbors = 5 distances = 0.1metric = euclidean


Hyperparameters: neighbors = 5 distances = 0.5metric = euclidean


...

Hyperparameters: neighbors = 150 distances = 0metric = euclidean


Hyperparameters: neighbors = 150 distances = 0.001metric = euclidean


Hyperparameters: neighbors = 150 distances = 0.01metric = euclidean


Hyperparameters: neighbors = 150 distances = 0.1metric = euclidean


Hyperparameters: neighbors = 150 distances = 0.5metric = euclidean


Final UMAP

In [ ]:
u = umap.UMAP(n_components = 3, n_neighbors = 150, min_dist = 0.1, metric = "euclidean").fit_transform(resized_mfccs)
fig = px.scatter_3d(u, x=0, y=1, z=2, color = labels, title = "UMAP of MFCC")
fig.show()

clustering_metrics(labels, u)


ENGLISH standard deviation:  2.6841714
SPANISH standard deviation:  2.6295528
ARABIC standard deviation:  2.4705262
FRENCH standard deviation:  2.2971663
MANDARIN standard deviation:  2.601675
KOREAN standard deviation:  2.3872235


ENGLISH-SPANISH distance :  4.1748395
ENGLISH-ARABIC distance :  6.091547
ENGLISH-MANDARIN distance :  5.235067
ENGLISH-FRENCH distance :  3.241294
ENGLISH-KOREAN distance :  5.1002436
SPANISH-ARABIC distance :  1.9175593
SPANISH-MANDARIN distance :  1.0602789
SPANISH-FRENCH distance :  0.9442547
SPANISH-KOREAN distance :  0.92557573
ARABIC-MANDARIN distance :  0.8589389
ARABIC-FRENCH distance :  2.8528311
ARABIC-KOREAN distance :  0.9921988
MANDARIN-FRENCH distance :  2.0000267
MANDARIN-KOREAN distance :  0.13703527
FRENCH-KOREAN distance :  1.8643401


In [ ]:
#Variance explained by UMAP1
UMAP_matrix = pd.DataFrame(u[:, 0])
pls = PLSRegression(n_components = 1)
pls.fit(UMAP_matrix, nums)
y_pred = pls.predict(UMAP_matrix)
print(r2_score(nums, y_pred, multioutput = 'variance_weighted'))

UMAP_matrix = pd.DataFrame(u[:, 1])
pls = PLSRegression(n_components = 1)
pls.fit(UMAP_matrix, nums)
y_pred = pls.predict(UMAP_matrix)
print(r2_score(nums, y_pred, multioutput = 'variance_weighted'))

UMAP_matrix = pd.DataFrame(u[:, 2])
pls = PLSRegression(n_components = 1)
pls.fit(UMAP_matrix, nums)
y_pred = pls.predict(UMAP_matrix)
print(r2_score(nums, y_pred, multioutput = 'variance_weighted'))





0.18551283126563578
0.09671967954784101
0.012140221554196582
